<h1>Folium + Leaflet Workflow mit mehreren GeoJSON Dateien</h1>
<ul>
    <li>Scalierbar</li>
    <li>Modular</li>
    <li>Clean</li>
    <li>Flexibel</li>
</ul>

<h2>1. Prepare Your Imports and Data</h2>

In [12]:
import geopandas as gpd
import pandas as pd
import os
import folium
from shapely.geometry import Point

In [4]:
# Step 1: Define directory and GeoJSON layer names
data_dir = 'raw_data_geojson'
layers = ['gruenflaechen', 'toiletten', 'baeder', 'theater', 'give_boxen']

In [5]:
# Step 2: Load all GeoJSON files into a dictionary
gdfs = {
    layer: gpd.read_file(os.path.join(data_dir, f'{layer}.geojson'))
    for layer in layers
}

<h2>2. Initialize the Map Based on a Central Location</h2>
<p>You can center the map using the centroid of one or more layers:</p>

In [14]:
# Use centroid of all combined data for map center
all_points = gpd.GeoSeries(pd.concat([gdf.geometry for gdf in gdfs.values()], ignore_index=True))
center = [all_points.centroid.y.mean(), all_points.centroid.x.mean()]

C:\Users\Glen\AppData\Local\Temp\ipykernel_15728\842907085.py:3: UserWarning: Geometry is in a geographic CRS. Results from 'centroid' are likely incorrect. Use 'GeoSeries.to_crs()' to re-project geometries to a projected CRS before this operation.

  center = [all_points.centroid.y.mean(), all_points.centroid.x.mean()]


In [20]:
# Initialize the folium map
m = folium.Map(location=center, zoom_start=13)

<h2>3. Add Each Layer to the Map</h2>
<p>You can loop through each GeoDataFrame and add it to the map as a separate folium.GeoJson layer:</p>

In [26]:
for name, gdf in gdfs.items():
    folium.GeoJson(
        gdf,
        name=name.capitalize(),
        tooltip=folium.GeoJsonTooltip(fields=gdf.columns.difference(['geometry']).tolist())
    ).add_to(m)

<h2>4. Add Layer Control and Display the Map</h2>

In [29]:
# Add a layer control toggle
folium.LayerControl().add_to(m)

In [31]:
m